# NTDS Data Clean Up
by Vitto Resnick, UCSF, 2025

## Import Necessary Dependencies/Packages \& Define Utilities/Functions

In [1]:
#Install this once (this is used to call info on icd10 codes)
!pip install icd10-cm

In [99]:
#Import necessary dependencies
import numpy as np
import pandas as pd
import icd10
from scipy.stats import chi2_contingency

def csc(str): #comma-separated codes to list 'S32.52,S82.90' -> ['S32.52','S82.90']
    list_of_codes = []
    if not "," in str:
        list_of_codes.append(str)
    else:
        list_of_codes=str.split(',')
    return list_of_codes

def find_unique_codes(list,search_term,n = None): #n characters to include #this is just used for my dbugging & querying icds
    unique_codes = []
    for patient in range(len(list)):
        if isinstance(list[patient],str):
            #print(list[patient])
            this_patients_codes = csc(list[patient])
            for code in range(len(this_patients_codes)):
                if (not this_patients_codes[code][:n] in unique_codes) and (search_term in this_patients_codes[code]):
                    unique_codes.append(this_patients_codes[code][:n])
        else:
            continue
    return unique_codes

def print_diagnoses(list_of_codes): #this is just used for my dbugging & querying icds
    sd_list = sorted(list_of_codes)
    unique_diagnoses = []

    for i in range(len(sd_list)):
        #print(sd_unique[i])
        try:
            code = sd_list[i]
            diagnosis = icd10.find(code).description
        except:
            try:
                code = sd_list[i][:7]
                diagnosis = icd10.find(code).description
            except:
                try:
                    code = sd_list[i][:6]
                    diagnosis = icd10.find(code).description
                except:
                    try:
                        code = sd_list[i][:5]
                        diagnosis = icd10.find(code).description
                    except:
                        try:
                            code = sd_list[i][:3]
                            diagnosis = icd10.find(code).description
                        except:
                            print("cant find this code!")
        
        if not diagnosis in unique_diagnoses:
            unique_diagnoses.append(diagnosis)
            print(code,": ",diagnosis)
        
        #if not "racture" in diagnosis:
        #    print("This diagnosis doesnt have the word fracture! - ",diagnosis)
    
    #print("These are all of the unique diagnoses")
    #print(unique_diagnoses)

#try this code if you want an example of what I was doing this for. 3 means you only look at the part of codes before the period
#current = sorted(find_unique_codes(list(df['primaryecodeicd10'].unique()),"",3))
#print_diagnoses(current)

def anycomp(list): #any complications in this list of booleans?  [0 0 0 0] false [0 0 1 0] true
    N = 0
    for i in range(len(list)):
        if list[i] == 'Yes' or list[i] == 'True' or list[i] == True or list[i] == '1' or list[i] == 1:
            N+=1
        elif list[i] == 'No' or list[i] == 'False' or list[i] == False or list[i] == '0' or list[i] == 0:
            N+=0
    if N>=1:
        return True
    else:
        return False

def calculate(dataframe,factor,Ns,calculate_pvalue=False):
    row = []
    row.append(str(sum(df.loc[df["ILE"] == True][factor]))+" ("+str(round(sum(df.loc[df["ILE"] == True][factor])/Ns[0]*100,1))+"%)")
    row.append(str(sum(df.loc[df["MLE"] == True][factor]))+" ("+str(round(sum(df.loc[df["MLE"] == True][factor])/Ns[1]*100,1))+"%)")
    row.append(str(sum(df.loc[df["ULE"] == True][factor]))+" ("+str(round(sum(df.loc[df["ULE"] == True][factor])/Ns[2]*100,1))+"%)")
    if calculate_pvalue == True:
        obs = np.array([[sum(df.loc[df["ILE"] == True][factor]), 
                         sum(df.loc[df["MLE"] == True][factor]), 
                         sum(df.loc[df["ULE"] == True][factor])], [
                        Ns[0]-sum(df.loc[df["ILE"] == True][factor]), 
                        Ns[1]-sum(df.loc[df["MLE"] == True][factor]), 
                        Ns[2]-sum(df.loc[df["ULE"] == True][factor])]]) 
        pval = round(chi2_contingency(obs).pvalue,3)
        if pval == 0:
            pval = "<0.001"
        row.append(pval)
    return row

def progressbar(progress,total): #animation to see speed of processing
    percent = 100*(progress/float(total))
    bar='█'*int(percent)+'-'*(100-int(percent))
    print(f"\r|{bar}|{percent:.2f}%",end="\r")

## Define ICD10 Code Cateogories and Other Dictionaries

In [5]:
#Categories of LE Injury
#the "sharfman_..._..." lists are names of the new columns to be added
#the LE_ and UE_ dictionaries take an icd10 prefix and direct which column to assign true for a given patient

#S32: Fracture of lumbar spine and pelvis
sharfman_LE_S32 = ['Fracture of acetabulum',                                      #S32.4 Fracture of acetabulum
                   'Fracture of pubis',                                           #S32.5 Fracture of pubis
                   'Fracture of ilium',                                           #S32.3 Fracture of ilium
                   'Fracture of ischium',                                         #S32.6 Fracture of ischium
                   'Fracture of pelvis multiple w/ disruption of pelvic circle',  #S32.81 Multiple fractures of pelvis with disruption of pelvic ring
                   'Fracture of pelvis without disruption of pelvic circle',      #S32.82 Multiple fractures of pelvis without disruption of pelvic ring
                   'Fracture of pelvis, other']                                   #S32.88 Fracture of other parts of pelvis - no desc
                                                                                  #S32.89 Fracture of other parts of pelvis
                                                                                  #S32.9  Fracture of unspecified parts of lumbosacral spine and pelvis

LE_dict =      dict.fromkeys(['S32.4']                          , 'Fracture of acetabulum')
LE_dict.update(dict.fromkeys(['S32.5']                          , 'Fracture of pubis'))
LE_dict.update(dict.fromkeys(['S32.3']                          , 'Fracture of ilium'))
LE_dict.update(dict.fromkeys(['S32.6']                          , 'Fracture of ischium'))
LE_dict.update(dict.fromkeys(['S32.81']                         , 'Fracture of pelvis multiple w/ disruption of pelvic circle'))
LE_dict.update(dict.fromkeys(['S32.82']                         , 'Fracture of pelvis without disruption of pelvic circle'))
LE_dict.update(dict.fromkeys(['S32.88','S32.89','S32.9','S32.8'], 'Fracture of pelvis, other'))


#S72: Fracture of femur
sharfman_LE_S72 = ['Fracture of femoral neck',         #S72.00 Fracture of unspecified part of neck of femur
                                                       #S72.01 Unspecified intracapsular fracture of femur
                                                       #S72.02 Fracture of epiphysis (separation) (upper) of femur
                                                       #S72.03 Midcervical fracture of femur
                                                       #S72.04 Fracture of base of neck of femur
                   'Fracture of other parts of femur'] #S72.05 Unspecified fracture of head of femur
                                                       #S72.06 Articular fracture of head of femur
                                                       #S72.08 Fracture of head and neck of femur - no desc
                                                       #S72.09 Other fracture of head and neck of femur
                                                       #S72.1  Pertrochanteric fracture
                                                       #S72.2  Subtrochanteric fracture of femur
                                                       #S72.3  Fracture of shaft of femur
                                                       #S72.4  Fracture of lower end of femur
                                                       #S72.8  Other fracture of femur
                                                       #S72.9  Unspecified fracture of femur
LE_dict.update(dict.fromkeys(['S72.00','S72.01','S72.02','S72.03','S72.04'], 'Fracture of femoral neck'))
LE_dict.update(dict.fromkeys(['S72.05','S72.06','S72.08','S72.09','S72.1',
                             'S72.2','S72.3','S72.4','S72.8','S72.9'], 'Fracture of other parts of femur'))

#S82: Fracture of lower leg, including ankle
sharfman_LE_S82 = ['Fracture of patella',###############S82.0 Fracture of patella
                   'Fracture of tibia and fibula',######S82.1 Fracture of upper end of tibia
                                                       #S82142A Bicondylar fracture of tibia
                                                       #S82.2 Fracture of shaft of tibia
                                                       #S82.3 Fracture of lower end of tibia
                   
                                                       #S89.0 Physeal fracture of upper end of tibia
                                                       #S89.1 Physeal fracture of lower end of tibia
                                                       #S89.2 Physeal fracture of upper end of fibula
                                                       #S89.3 Physeal fracture of lower end of fibula
                   
                                                       #S82.87 Pilon fracture of tibia
                   
                                                       #S82.4 Fracture of shaft of fibula
                   
                                                       #S82.81 Torus fracture of upper end of fibula
                                                       #S82.82 Torus fracture of lower end of fibula
                                                       #S82.83 Other fracture of upper and lower end of fibula
                                                       #S82.86 Maisonneuve's fracture
                   
                   'Fracture of ankle']#################S82.5 Fracture of medial malleolus
                                                       #S82.6 Fracture of lateral malleolus
                                                       #S82.84 Bimalleolar fracture of lower leg
                                                       #S82.85 Trimalleolar fracture of lower leg
LE_dict.update(dict.fromkeys(['S82.0'],                                              'Fracture of patella'))
LE_dict.update(dict.fromkeys(['S82.1','S82142A','S82.2','S82.3',
                              'S89.0','S89.1','S89.2','S89.3',
                              'S82.87','S82.4','S82.81','S82.82','S82.83','S82.86'], 'Fracture of tibia and fibula'))
LE_dict.update(dict.fromkeys(['S82.5','S82.6','S82.84','S82.85'],                    'Fracture of ankle'))


#S92: Fracture of foot and toe, except ankle
#S89: Other and unspecified injuries of lower leg
sharfman_LE_other = ['Fracture of LE, other']     #S82.88 Other fractures of lower leg - No desc
                                                  #S82.89 Other fractures of lower leg
                                                  #S82.9 Unspecified fracture of lower leg
                                                  #S92: Fracture of foot and toe, except ankle
                                                  #S89.8: Other specified injuries of lower leg
                                                  #S89.9: Unspecified injury of lower leg
LE_dict.update(dict.fromkeys(['S82.88','S82.89','S82.9','S92','S89.8','S89.9'], 'Fracture of LE, other'))

#List of columns to add
sharfman_LE = sharfman_LE_S32 + sharfman_LE_S72 + sharfman_LE_S82 + sharfman_LE_other

In [7]:
#Categories of UE Injury
#the "sharfman_..._..." lists are names of the new columns to be added
#the LE_ and UE_ dictionaries take an icd10 prefix and direct which column to assign true for a given patient

#S42: Fracture of shoulder and upper arm
sharfman_UE_S42 = ['Fracture of clavicle',        #S42.0 Fracture of clavicle
                   'Fracture of scapula',         #S42.1 Fracture of scapula
                   'Fracture of humerus']         #S42.2 Fracture of upper end of humerus
                                                  #S42.3 Fracture of shaft of humerus
                                                  #S42.4 Fracture of lower end of humerus
#S52: Fracture of forearm
sharfman_UE_S52 = ['Fracture of radius and ulna'] #S52 Fracture of forearm
#S62: Fracture at wrist and hand level
sharfman_UE_S62 = ['Fracture of Carpal bones']    #S62 Fracture at wrist and hand level

sharfman_UE_other = ['Fracture of UE, other']        #S42.9 Fracture of shoulder girdle, part unspecified

UE_dict =      dict.fromkeys(['S42.0']                 , 'Fracture of clavicle')
UE_dict.update(dict.fromkeys(['S42.1']                 , 'Fracture of scapula'))
UE_dict.update(dict.fromkeys(['S42.2', 'S42.3','S42.4'], 'Fracture of humerus'))
UE_dict.update(dict.fromkeys(['S52']                   , 'Fracture of radius and ulna'))
UE_dict.update(dict.fromkeys(['S62']                   , 'Fracture of Carpal bones'))
UE_dict.update(dict.fromkeys(['S42.9']                 , 'Fracture of UE, other'))

sharfman_UE = sharfman_UE_S42+sharfman_UE_S52+sharfman_UE_S62+sharfman_UE_other

In [9]:
#True for "fall on same level - other" #not this only accounts for mechanism codes that begin with W (only ones pertaining to falls)
fall_same_level = [
"W00.0",#:  Fall on same level due to ice and snow
"W01",  #:  Fall on same level from slipping, tripping and stumbling
"W03"   #:  Other fall on same level due to collision with another person
         ]

other_falls = [
"W00.1",#:  Fall from stairs and steps due to ice and snow
"W00.2",#:  Other fall from one level to another due to ice and snow
"W00.9",#:  Unspecified fall due to ice and snow
"W04",#:  Fall while being carried or supported by other persons
"W05",#:  Fall from non-moving wheelchair, nonmotorized scooter and motorized mobility scooter
"W06",#:  Fall from bed
"W07",#:  Fall from chair
"W08",#:  Fall from other furniture
"W09",#:  Fall on and from playground equipment
"W10",#:  Fall on and from stairs and steps
"W11",#:  Fall on and from ladder
"W12",#:  Fall on and from scaffolding
"W13",#:  Fall from, out of or through building or structure
"W14",#:  Fall from tree
"W15",#:  Fall from cliff
"W16",#:  Fall, jump or diving into water
"W17",#:  Other fall from one level to another
"W18",#:  Other slipping, tripping and stumbling and falls
"W19"#:  Unspecified fall
]

for_sure_reject = [
"W20",#:  Struck by thrown, projected or falling object
"W21",#:  Striking against or struck by sports equipment
"W22",#:  Striking against or struck by other objects
"W23",#:  Caught, crushed, jammed or pinched in or between objects
"W24",#:  Contact with lifting and transmission devices, not elsewhere classified
"W25",#:  Contact with sharp glass
"W26",#:  Contact with other sharp objects
"W27",#:  Contact with nonpowered hand tool
"W28",#:  Contact with powered lawn mower
"W29",#:  Contact with other powered hand tools and household machinery
"W30",#:  Contact with agricultural machinery
"W31",#:  Contact with other and unspecified machinery
"W32",#:  Accidental handgun discharge and malfunction
"W33",#:  Accidental rifle, shotgun and larger firearm discharge and malfunction
"W34",#:  Accidental discharge and malfunction from other and unspecified firearms and guns
"W36",#:  Explosion and rupture of gas cylinder
"W37",#:  Explosion and rupture of pressurized tire, pipe or hose
"W38",#:  Explosion and rupture of other specified pressurized devices
"W39",#:  Discharge of firework
"W40",#:  Explosion of other materials
"W45",#:  Foreign body or object entering through skin
"W49",#:  Exposure to other inanimate mechanical forces
"W50",#:  Accidental hit, strike, kick, twist, bite or scratch by another person
"W51",#:  Accidental striking against or bumped into by another person
"W52",#:  Crushed, pushed or stepped on by crowd or human stampede
"W54",#:  Contact with dog
"W55",#:  Contact with other mammals
"W56",#:  Contact with nonvenomous marine animal
"W57",#:  Bitten or stung by nonvenomous insect and other nonvenomous arthropods
"W58",#:  Contact with crocodile or alligator
"W59",#:  Contact with other nonvenomous reptiles
"W60",#:  Contact with nonvenomous plant thorns and spines and sharp leaves
"W61",#:  Contact with birds (domestic) (wild)
"W64",#:  Exposure to other animate mechanical forces
"W85",#:  Exposure to electric transmission lines
"W86",#:  Exposure to other specified electric current
"W94"]#:  Exposure to high and low air pressure and changes in air pressure

fall_same_level_dict =      dict.fromkeys(fall_same_level            ,True)
fall_same_level_dict.update(dict.fromkeys(other_falls+for_sure_reject,False))
fall_dict =      dict.fromkeys(fall_same_level+other_falls, True)
fall_dict.update(dict.fromkeys(for_sure_reject            ,False))

In [11]:
mech_cats = ["Mechanism-Fall","MVT Motorcyclist","MVT Occupant","MVT Other","MVT Pedal cyclist","MVT Pedestrian","MVT Unspecified",
            "Machinery","Struck by, against","Pedal cyclist, other","Pedestrian, other","Transport, other","Mechanism-Other"]
mech_dict =      dict.fromkeys([1,2,4,5,6,17,18,19,20,22,23,24,26,27],"Mechanism-Other")
mech_dict.update(dict.fromkeys([3 ],"Mechanism-Fall"))
mech_dict.update(dict.fromkeys([7 ],"Machinery"))
mech_dict.update(dict.fromkeys([8 ],"MVT Occupant"))
mech_dict.update(dict.fromkeys([9 ],"MVT Motorcyclist"))
mech_dict.update(dict.fromkeys([10],"MVT Pedal cyclist"))
mech_dict.update(dict.fromkeys([11],"MVT Pedestrian"))
mech_dict.update(dict.fromkeys([12],"MVT Unspecified"))
mech_dict.update(dict.fromkeys([13],"MVT Other"))
mech_dict.update(dict.fromkeys([14],"Pedal cyclist, other"))
mech_dict.update(dict.fromkeys([15],"Pedestrian, other"))
mech_dict.update(dict.fromkeys([16],"Transport, other"))
mech_dict.update(dict.fromkeys([21],"Struck by, against"))

In [134]:
mech_dict[9]

'MVT Motorcyclist'

In [160]:
df.iloc[17]

inc_key                         170000016633
LE_Dcode                            S72.452A
UE_Dcode                                 NaN
Fracture Type                            ILE
ILE                                     True
                                    ...     
Schizoaffective Disorder T-F           False
Schizophrenia                            NaN
Schizophrenia T-F                      False
Delirium                                 NaN
mFI_5                                      5
Name: 17, Length: 169, dtype: object

In [23]:
sex_dict =      dict.fromkeys(["Male"  ,"1.0",1],"Sex-Male")
sex_dict.update(dict.fromkeys(["Female","2.0",2],"Sex-Female"))
sex_dict.update(dict.fromkeys([               3],"Sex-Nonbinary"))
race_dict =      dict.fromkeys(['White, Hispanic','White, non-Hispanic']             ,"Race-White")
race_dict.update(dict.fromkeys(['Black or African American']                         ,"Race-Black"))
race_dict.update(dict.fromkeys(['Other','Pacific Islander','American Indian','Asian'],"Race-Other"))

## Import Data \& Add New Columns

In [344]:
#Plan
#Race - sep columns, remove Unknown - DONE
#Sex - sep columns, remove nan - DONE
#Fracture Type - sep columns - DONE but check if needed - acc. Tim SKIP
#Payment Method - sep columns, remove nan -  DONE
#GCS - check for unknowns - DONE
#Fall on the same level other - DONE
#Mechanism - TO DO
#ISS - T/F for each of 3 ranges - acc. Tim SKIP 
#Hospital Discharge - Discharge to inpatient rehab T/F - DONE
#ICU Days - longer than 3 days T/F - DONE
#New col: any complications T/F - DONE
#Remove nan/unknown patients - DONE
#Decode diagnoses + new columns - DONE

In [164]:
df = pd.read_csv('geriatric_processed_data_17_23.csv')
N = len(df)

#Insert new columns
for i in range(len(sharfman_LE)): #sharfman labels for LE fractures
    df.insert(4+i,sharfman_LE[i],False)

for i in range(len(sharfman_UE)): #sharfman labels for UE fractures
    df.insert(4+len(sharfman_LE)+i,sharfman_UE[i],False)

fracture_groups = ["ILE","MLE","ULE"] #this is to add new T/F columns for ILE, MLE, ULE
for i in range(len(fracture_groups)):
    df.insert(df.columns.get_loc("Fracture Type")+1+i,fracture_groups[i],False)

#df.insert(df.columns.get_loc("Race Complete")+1,"Race Filtered","Other")
races = ["Race-White","Race-Black","Race-Other","Hispanic"]
for i in range(len(races)):
    df.insert(df.columns.get_loc("Race Complete")+1+i,races[i],False)

sexes = ["Sex-Male","Sex-Female","Sex-Nonbinary"]
for i in range(len(sexes)):
    df.insert(df.columns.get_loc("SEX")+1+i,sexes[i],False)

df.insert(df.columns.get_loc("primaryecodeicd10")+1,"fall on same level - other",False)
df.insert(df.columns.get_loc("primaryecodeicd10")+2,"any fall",False)

for i in range(len(mech_cats)):
    df.insert(df.columns.get_loc("mechanism")+1+i,mech_cats[i],False)
    
payment_methods = ['Payment-Medicare','Payment-Private/Commercial Insurance','Payment-Medicaid','Payment-Other Government','Payment-Self-Pay','Payment-Other','Payment-Not Billed (for any reason)']
for i in range(len(payment_methods)):
    df.insert(df.columns.get_loc("primarymethodpayment")+1+i,payment_methods[i],False)

df.insert(df.columns.get_loc("hospdischargedisposition")+1,"discharge_to_rehab",False)

df.insert(df.columns.get_loc("totaliculos")+1,"long_ICU",False)

df.insert(df.columns.get_loc("Ventilator-Associated Pneumonia")+1,"Any Complications",False)


df.insert(df.columns.get_loc("Pregnancy")+1,                                                "Pregnancy T-F",False)
df.insert(df.columns.get_loc("Bipolar I/II Disorder")+1,                        "Bipolar I/II Disorder T-F",False)
df.insert(df.columns.get_loc("Major Depressive Disorder")+1,                "Major Depressive Disorder T-F",False)
df.insert(df.columns.get_loc("Other Mental/Personality Disorder")+1,"Other Mental/Personality Disorder T-F",False)
df.insert(df.columns.get_loc("Post-Traumatic Stress Disorder")+1,      "Post-Traumatic Stress Disorder T-F",False)
df.insert(df.columns.get_loc("Schizoaffective Disorder")+1,                  "Schizoaffective Disorder T-F",False)
df.insert(df.columns.get_loc("Schizophrenia")+1,                                        "Schizophrenia T-F",False)

comorbities = ['Attention Deficit Hyperactivity Disorder', 'Advanced Directive Limiting Care', 
               'Alcohol Use Disorder', 'Angina Pectoris', 'Anticoagulant Therapy', 'Bleeding Disorder', 
               'Currently Receiving Chemotherapy for Cancer', 'Cirrhosis', 'Congenital Anomalies', 
               'Chronic Obstructive Pulmonary Disease', 'Cerebrovascular Accident', 'Dementia', 'Diabetes Mellitus', 
               'Disseminated Cancer', 'Functionaly Dependent Health Status', 'Congestive Heart Failure', 'Hypertension', 
               'Myocardial Infarction_pc', 'Other_pc', 'Peripheral Arterial Disease', 'Prematurity', 'Mental/Personality Disorder', 
               'Chronic Renal Failure', 'Current Smoker', 'Steroid Use', 'Substance Abuse Disorder']

for i in range(len(comorbities)):
    df.insert(df.columns.get_loc(comorbities[i])+1,comorbities[i]+" T-F",False)
    
for i in range(len(list(df["GCS"].unique()))):
    df.insert(df.columns.get_loc("GCS")+1+i,list(df["GCS"].unique())[i],False)

for i in range(len(list(df["ISS"].unique()))):
    df.insert(df.columns.get_loc("ISS")+1+i,list(df["ISS"].unique())[i],False)

print(df.columns.tolist()) #confirm the new columns were added in the order you like

/var/folders/df/bkrdvvkx4gv6xg_gbdp7x9x80000gr/T/ipykernel_83290/2207029360.py:1: DtypeWarning: Columns (4,5,7,9,16,17,20,22,23,24,25,26,27,29,30,31,32,33,34,35,36,37,39,40,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64,65,66,67,68,77) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('geriatric_processed_data_17_23.csv')


['inc_key', 'LE_Dcode', 'UE_Dcode', 'Fracture Type', 'ILE', 'MLE', 'ULE', 'Fracture of acetabulum', 'Fracture of pubis', 'Fracture of ilium', 'Fracture of ischium', 'Fracture of pelvis multiple w/ disruption of pelvic circle', 'Fracture of pelvis without disruption of pelvic circle', 'Fracture of pelvis, other', 'Fracture of femoral neck', 'Fracture of other parts of femur', 'Fracture of patella', 'Fracture of tibia and fibula', 'Fracture of ankle', 'Fracture of LE, other', 'Fracture of clavicle', 'Fracture of scapula', 'Fracture of humerus', 'Fracture of radius and ulna', 'Fracture of Carpal bones', 'Fracture of UE, other', 'TEACHINGSTATUS', 'HOSPITALTYPE', 'Race Complete', 'Race-White', 'Race-Black', 'Race-Other', 'Hispanic', 'BEDSIZE', 'VERIFICATIONLEVEL', 'SEX', 'Sex-Male', 'Sex-Female', 'Sex-Nonbinary', 'GCS', 'GCS 13-15', 'GCS 9-12', 'GCS <=8', 'primaryecodeicd10', 'fall on same level - other', 'any fall', 'ecode_desc', 'mechanism', 'Mechanism-Fall', 'MVT Motorcyclist', 'MVT Occu

In [17]:
print(list(df['Pregnancy'].unique()))
print(list(df['Bipolar I/II Disorder'].unique()))
print(list(df['Major Depressive Disorder'].unique()))
print(list(df['Other Mental/Personality Disorder'].unique()))
print(list(df['Post-Traumatic Stress Disorder'].unique()))
print(list(df['Schizoaffective Disorder'].unique()))
print(list(df['Schizophrenia'].unique()))
print(list(df['Delirium'].unique()))

[nan, 38.0]
[nan, 39.0]
[nan, 40.0]
[nan, 41.0]
[nan, 42.0]
[nan, 43.0]
[nan, 44.0]
[nan, False, True]


## Remove Patients with Missing Data

In [19]:
#Removal Criteria

remove = []
for index, patient in df.iterrows():

    #Race - Unknown
    if patient["Race Complete"] == 'Unknown':
        remove.append(index)
        print("Remove patient ",index," - basis: race ",patient["Race Complete"])
    #Primary Method Payment - NaN
    if str(patient['primarymethodpayment']) == 'nan':
        remove.append(index)
        print("Remove patient ",index," - basis: payment ",patient["primarymethodpayment"])
    #Sex - NaN
    if str(patient['SEX']) == 'nan':
        remove.append(index)
        print("Remove patient ",index," - basis: SEX ",patient["SEX"])
    #eddischargedisposition - NaN
    if str(patient['eddischargedisposition']) == 'nan':
        remove.append(index)
        print("Remove patient ",index," - basis: eddischargedisposition ",patient["eddischargedisposition"])
    #hospdischargedisposition - NaN
    if str(patient['hospdischargedisposition']) == 'nan':
        remove.append(index)
        print("Remove patient ",index," - basis: hospdischargedisposition ",patient["hospdischargedisposition"])
    if str(patient['mechanism'])=='nan':
        remove.append(index)
        print("Remove patient ",index," - basis: mechanism ",patient["mechanism"])
    #Spinal Injury
    LE_codes = csc(patient['LE_Dcode'])
    for i in range(len(LE_codes)):
        code = LE_codes[i]
        if ("S32.0" in code or "S32.1" in code or "S32.2" in code): #ignore spine (not included in sharfman labels)
            if index not in remove: 
                remove.append(index)
                #print("Remove patient ",index," - basis: spine injury ",patient["LE_Dcode"])
    
df = df.drop(index=remove)
N2 = len(df)
print("Dropped ",len(remove)," patients. From ",N," to ",N2)

Remove patient  18  - basis: eddischargedisposition  nan
Remove patient  54  - basis: spine injury  S32.491A,S32.111A,S32.511A,S32.591A
Remove patient  65  - basis: mechanism  nan
Remove patient  83  - basis: hospdischargedisposition  nan
Remove patient  100  - basis: eddischargedisposition  nan
Remove patient  102  - basis: hospdischargedisposition  nan
Remove patient  138  - basis: eddischargedisposition  nan
Remove patient  161  - basis: spine injury  S32.111A
Remove patient  181  - basis: hospdischargedisposition  nan
Remove patient  183  - basis: spine injury  S32.19XA
Remove patient  185  - basis: hospdischargedisposition  nan
Remove patient  206  - basis: hospdischargedisposition  nan
Remove patient  231  - basis: spine injury  S32.17XA
Remove patient  239  - basis: eddischargedisposition  nan
Remove patient  269  - basis: spine injury  S32.810A,S32.10XA
Remove patient  282  - basis: spine injury  S32.110A,S32.592A
Remove patient  329  - basis: spine injury  S32.119A,S32.512A,S3

In [21]:
#Check to make sure no nan or unknown
print(list(df["Race Complete"].unique()))
print(list(df["primarymethodpayment"].unique()))
print(list(df["SEX"].unique()))
print(list(df["eddischargedisposition"].unique()))
print(list(df["hospdischargedisposition"].unique()))

['Other', 'White, Hispanic', 'White, non-Hispanic', 'Black or African American', 'Pacific Islander', 'American Indian', 'Asian']
['Medicare', 'Private/Commercial Insurance', 'Medicaid', 'Other Government', 'Self-Pay', 'Other', 'Not Billed (for any reason)', 'Private/Commerical Insurance']
['Female', 'Male', '2.0', '1.0', 2.0, 1.0, 3.0]
['Operating Room', 'Floor bed (general admission, non-specialty unit bed', 'Observation unit (unit that provides < 24 hour stays)', 'Telemetry/step-down unit (less acuity than ICU)', 'Intensive Care Unit (ICU)', '7.0', '8.0', '1.0', '3.0', '2.0', 1.0, 3.0, 7.0, 2.0, 8.0]
['Discharged/Transferred to inpatient rehab or designated unit', 'Deceased/Expired', 'Discharged to home or self-care (routine discharge)', 'Discharged/Transferred to home under care of organized home health service', 'Discharged/Transferred to hospice care', 'Discharged/Transferred to Skilled Nursing Facility (SNF)', 'Discharged/Transferred to Long Term Care Hospital (LTCH)', 'Discharge

## Assign T/F Values to Metadata Columns

In [25]:
#New Columns: Race, , Sex, Payment, days ICU, discharge to rehab

for index, patient in df.iterrows():
    
    race = patient["Race Complete"]
    df.loc[index,race_dict[race]] = True
    if race == 'White, Hispanic':
        df.loc[index,"Hispanic"] = True

    sex = patient["SEX"]
    df.loc[index,sex_dict[sex]] = True

    payment = patient['primarymethodpayment']
    if payment == "Private/Commerical Insurance":
        df.loc[index,"Payment-Private/Commercial Insurance"] = True
    else: 
        df.loc[index,"Payment-"+payment] = True

    discharge = patient['hospdischargedisposition']
    if (discharge == "Discharged/Transferred to inpatient rehab or designated unit") or (discharge == '11.0') or (discharge == 11): #or ('11' in discharge)
        df.loc[index,"discharge_to_rehab"] = True
        
    icu_length = patient['totaliculos']
    if icu_length == '>3d':
        df.loc[index,"long_ICU"] = True
    elif icu_length == '<=3d':
        df.loc[index,"long_ICU"] = False

    #Any complications from deep ssi to ventilator associated pneumonia
    df.loc[index,"Any Complications"]= anycomp(list(df.loc[index,"Central Line-associated Bloodstream Infection":"Ventilator-Associated Pneumonia"]))

    #Data Cleanup for Pregnancy to Schizophrenia
    query0 = ['Pregnancy T-F','Bipolar I/II Disorder T-F','Major Depressive Disorder T-F','Other Mental/Personality Disorder T-F',
             'Post-Traumatic Stress Disorder T-F','Schizoaffective Disorder T-F','Schizophrenia T-F']
    for i in range(len(query0)):
        if str(patient[query0[i][:-4]])=='nan':
            df.loc[index,query0[i]] = False
        else:
            df.loc[index,query0[i]] = True

    df.loc[index,patient["GCS"]] = True
    df.loc[index,patient["ISS"]] = True
    #progressbar(index+1,N2)

## Assign T/F Values to Diagnosis Columns based on icd10 codes

In [62]:
#ICD10 codes to T/F diagnoses, mechanisms
for index, patient in df.iterrows():

    #Pull codes
    LE_codes = csc(patient['LE_Dcode'])
    if isinstance(patient['UE_Dcode'],str):
        UE_codes = csc(patient['UE_Dcode'])
    else:
        UE_codes = []

    #ILE,MLE,ULE Types
    if   len(LE_codes) >= 1 and len(UE_codes) >= 1:
        fracture_type  = "ULE"
        df.loc[index,"ULE"] = True
    elif len(LE_codes) >  1 and len(UE_codes) == 0:
        fracture_type  = "MLE"
        df.loc[index,"MLE"] = True
    elif len(LE_codes) == 1 and len(UE_codes) == 0:
        fracture_type  = "ILE"
        df.loc[index,"ILE"] = True
        #if patient['Fracture Type'] != "ILE": #so far no disagreements!
        #    print("ILE disaggreement for patient ",index,", LE codes: ",patient['LE_Dcode'],", UE codes: ",patient['UE_Dcode'],", fracture type: ",patient['Fracture Type'])
        #    break
    #else: #so far not an issue!
    #    print("couldn't assign fracture type to patient ",index,", LE codes: ",patient['LE_Dcode'],", UE codes: ",patient['UE_Dcode'])
    #    break

    #Decode LE ICD10s and assign trues to appropriate columns
    for i in range(len(LE_codes)):
        code = LE_codes[i]
        
        try:
            search = code #S82.231A
            diagnosis = LE_dict[search]
        except:
            try: 
                search = code[:7] #S82.231
                diagnosis = LE_dict[search]
            except: 
                try:
                    search = code[:6] #S82.23
                    diagnosis = LE_dict[search]
                except:
                    try: 
                        search = code[:5] #S82.2
                        diagnosis = LE_dict[search]
                    except:
                        try:
                            search = code[:3] #S82
                            diagnosis = LE_dict[search]
                        except:
                            print("Cant match a diagnosis to this code! - LE ",code)
        df.loc[index,diagnosis] = True

    #Decode UE ICD10s and assign trues to appropriate columns
    for i in range(len(UE_codes)):
        code = UE_codes[i]
        try: 
            search = code[:5]
            diagnosis = UE_dict[search]
        except:
            try:
                search = code[:3]
                diagnosis = UE_dict[search]
            except:
                print("Cant match a diagnosis to this code! - UE ",code)
        df.loc[index,diagnosis] = True

    #Decode mechanism code for fall on same level other?
    w_code = patient['primaryecodeicd10']
    try: 
        search = w_code[:5]
        df.loc[index,"fall on same level - other"] = fall_same_level_dict[search]
    except:
        try:
            search = w_code[:3]
            df.loc[index,"fall on same level - other"] = fall_same_level_dict[search]
        except:
            continue
            
    #mechanism - fall or?
    mechanism_no = patient['mechanism']
    mechanism = mech_dict[mechanism_no]
    print("Patient ",index," mechanism: ",mechanism_no," ",mechanism)
    df.loc[index,mechanism] = True
    
    #comorbidities
    for j in range(len(comorbities)):
        value = df.loc[index,comorbities[j]]
        try:
            if float(value) >= 1:
                df.loc[index,comorbities[j]+" T-F"] = True
            #elif float(value) == 0:
            #    df.loc[index,comorbities[j]+" T-F"] = False
        except:
            if value == "True":
                df.loc[index,comorbities[j]+" T-F"] = True
            #elif value == "False" or str(value)=='nan':
            #    df.loc[index,comorbities[j]+" T-F"] = False

### Check for Correct Assignment 

In [99]:
df.loc[766903,'LE_Dcode']

'S82.141A,S82.831A'

In [111]:
print(icd10.find("S82.141A").description)

Displaced bicondylar fracture of right tibia, initial encounter for closed fracture


In [107]:
df.loc[766903,'Fracture of tibia and fibula']

True

In [113]:
df.loc[4,'LE_Dcode']

'S92.352A,S82.235A,S82.432A,S82.234A,S82.431A'

In [117]:
print(icd10.find("S82.235A").description)

Nondisplaced oblique fracture of shaft of left tibia, initial encounter for closed fracture


In [119]:
df.iloc[4]['Fracture of tibia and fibula']

True

## Table 1

In [101]:
#Generate Table 1
factors1 = ["Sex-Female"]+races+comorbities+payment_methods
table1 = pd.DataFrame(columns = fracture_groups+['p-value'],
                     index=['N']+factors1)

Ns = [len(df.loc[df["ILE"] == True]),
      len(df.loc[df["MLE"] == True]),
      len(df.loc[df["ULE"] == True])]
table1.loc['N'] = Ns+[None] #check sum(Ns)

table1.loc["Sex-Female"] = calculate(df,"Sex-Female",Ns,True)
for i in range(len(races)):
    table1.loc[races[i]] = calculate(df,races[i],Ns,True)
for i in range(len(comorbities)):
    table1.loc[comorbities[i]] = calculate(df,comorbities[i]+" T-F",Ns,True)
for i in range(len(payment_methods)):
    table1.loc[payment_methods[i]] = calculate(df,payment_methods[i],Ns,True)

table1

ILE            MLE  \
N                                                    534053         101167   
Sex-Female                                   365045 (68.4%)  66033 (65.3%)   
Race-White                                   349496 (65.4%)  64130 (63.4%)   
Race-Black                                     19802 (3.7%)    5110 (5.1%)   
Race-Other                                   164755 (30.8%)  31927 (31.6%)   
Hispanic                                       12419 (2.3%)    2574 (2.5%)   
Attention Deficit Hyperactivity Disorder        1043 (0.2%)     224 (0.2%)   
Advanced Directive Limiting Care               10412 (1.9%)    1543 (1.5%)   
Alcohol Use Disorder                           14154 (2.7%)    2895 (2.9%)   
Angina Pectoris                                 1639 (0.3%)     272 (0.3%)   
Anticoagulant Therapy                        112447 (21.1%)  18698 (18.5%)   
Bleeding Disorder                               8425 (1.6%)    1407 (1.4%)   
Currently Receiving Chemotherapy for Cancer     5639 (1.1%)     816 (0.8%)   
Cirrhosis                                       6175 (1.2%)    1250 (1.2%)   
Congenital Anomalies                             289 (0.1%)      57 (0.1%)   
Chronic Obstructive Pulmonary Disease         82200 (15.4%)  13835 (13.7%)   
Cerebrovascular Accident                       30643 (5.7%)    4766 (4.7%)   
Dementia                                      88844 (16.6%)  10193 (10.1%)   
Diabetes Mellitus                            132344 (24.8%)  24541 (24.3%)   
Disseminated Cancer                             6976 (1.3%)     957 (0.9%)   
Functionaly Dependent Health Status          151745 (28.4%)  23882 (23.6%)   
Congestive Heart Failure                      55776 (10.4%)    9800 (9.7%)   
Hypertension                                 350617 (65.7%)  58706 (58.0%)   
Myocardial Infarction_pc                        6460 (1.2%)    1143 (1.1%)   
Other_pc                                       26923 (5.0%)    4978 (4.9%)   
Peripheral Arterial Disease                    14071 (2.6%)    2370 (2.3%)   
Prematurity                                       58 (0.0%)       7 (0.0%)   
Mental/Personality Disorder                    14749 (2.8%)    2654 (2.6%)   
Chronic Renal Failure                          19887 (3.7%)    3841 (3.8%)   
Current Smoker                                53215 (10.0%)    8810 (8.7%)   
Steroid Use                                    11296 (2.1%)    2097 (2.1%)   
Substance Abuse Disorder                        6362 (1.2%)    1143 (1.1%)   
Payment-Medicare                             448889 (84.1%)  80015 (79.1%)   
Payment-Private/Commercial Insurance          60674 (11.4%)  15606 (15.4%)   
Payment-Medicaid                                8904 (1.7%)    1945 (1.9%)   
Payment-Other Government                        7328 (1.4%)    1463 (1.4%)   
Payment-Self-Pay                                4036 (0.8%)     980 (1.0%)   
Payment-Other                                   4166 (0.8%)    1142 (1.1%)   
Payment-Not Billed (for any reason)               56 (0.0%)      16 (0.0%)   

                                                       ULE p-value  
N                                                    31751    None  
Sex-Female                                   23547 (74.2%)  <0.001  
Race-White                                   20793 (65.5%)  <0.001  
Race-Black                                      830 (2.6%)  <0.001  
Race-Other                                   10128 (31.9%)  <0.001  
Hispanic                                        769 (2.4%)  <0.001  
Attention Deficit Hyperactivity Disorder         40 (0.1%)   0.003  
Advanced Directive Limiting Care                599 (1.9%)  <0.001  
Alcohol Use Disorder                            736 (2.3%)  <0.001  
Angina Pectoris                                  77 (0.2%)   0.022  
Anticoagulant Therapy                         6258 (19.7%)  <0.001  
Bleeding Disorder                               442 (1.4%)  <0.001  
Currently Receiving Chemotherapy for C

## Table 2

In [126]:
factors2 = mech_cats+sharfman_LE+sharfman_UE+list(df["GCS"].unique())+list(df["ISS"].unique())
table2 = pd.DataFrame(columns = fracture_groups+['p-value'],
                     index=['N']+factors2)

Ns = [len(df.loc[df["ILE"] == True]),
      len(df.loc[df["MLE"] == True]),
      len(df.loc[df["ULE"] == True])]
table2.loc['N'] = Ns+[None] #check sum(Ns)


for i in range(len(factors2)):
    if sum(df[factors2[i]])==0:
        continue
    table2.loc[factors2[i]] = calculate(df,factors2[i],Ns,True)

table2

ILE  \
N                                                           534053   
Mechanism-Fall                                      500780 (93.8%)   
MVT Motorcyclist                                               NaN   
MVT Occupant                                                   NaN   
MVT Other                                                      NaN   
MVT Pedal cyclist                                              NaN   
MVT Pedestrian                                                 NaN   
MVT Unspecified                                                NaN   
Machinery                                               250 (0.0%)   
Struck by, against                                     4878 (0.9%)   
Pedal cyclist, other                                           NaN   
Pedestrian, other                                              NaN   
Transport, other                                               NaN   
Mechanism-Other                                        4549 (0.9%)   
Fracture of acetabulum                                 5694 (1.1%)   
Fracture of pubis                                     16053 (3.0%)   
Fracture of ilium                                      1296 (0.2%)   
Fracture of ischium                                     348 (0.1%)   
Fracture of pelvis multiple w/ disruption of pe...     3207 (0.6%)   
Fracture of pelvis without disruption of pelvic...     4832 (0.9%)   
Fracture of pelvis, other                              3216 (0.6%)   
Fracture of femoral neck                            159356 (29.8%)   
Fracture of other parts of femur                    267382 (50.1%)   
Fracture of patella                                    8866 (1.7%)   
Fracture of tibia and fibula                          21344 (4.0%)   
Fracture of ankle                                     36069 (6.8%)   
Fracture of LE, other                                  6390 (1.2%)   
Fracture of clavicle                                      0 (0.0%)   
Fracture of scapula                                       0 (0.0%)   
Fracture of humerus                                       0 (0.0%)   
Fracture of radius and ulna                               0 (0.0%)   
Fracture of Carpal bones                                  0 (0.0%)   
Fracture of UE, other                                     0 (0.0%)   
GCS 13-15                                           529035 (99.1%)   
GCS 9-12                                               4247 (0.8%)   
GCS <=8                                                 771 (0.1%)   

                                                               MLE  \
N                                                           101167   
Mechanism-Fall                                       82095 (81.1%)   
MVT Motorcyclist                                               NaN   
MVT Occupant                                                   NaN   
MVT Other                                                      NaN   
MVT Pedal cyclist                                              NaN   
MVT Pedestrian                                                 NaN   
MVT Unspecified                                                NaN   
Machinery                                               257 (0.3%)   
Struck by, against                                     1481 (1.5%)   
Pedal cyclist, other                                           NaN   
Pedestrian, other                                              NaN   
Transport, other                                               NaN   
Mechanism-Other                                        1899 (1.9%)   
Fracture of acetabulum                               15525 (15.3%)   
Fracture of pubis                                    21216 (21.0%)   
Fracture of ilium                                      2880 (2.8%)   
Fracture of ischium                                     916 (0.9%)   
Fracture of pelvis multiple w/ disruption of pe...     1790 (1.8%)   
Fracture of pelvis without disruption of pelvic...     2180 (2.2%)   
Fr

In [162]:
sorted(list(df["ISS"].unique()))

['ISS 16-25', 'ISS <=15', 'ISS>25']

## Export cleaned dataset as csv

In [171]:
# Check all the columns you want are there
print(df.columns.tolist())

['inc_key', 'LE_Dcode', 'UE_Dcode', 'Fracture Type', 'ILE', 'MLE', 'ULE', 'Fracture of acetabulum', 'Fracture of pubis', 'Fracture of ilium', 'Fracture of ischium', 'Fracture of pelvis multiple w/ disruption of pelvic circle', 'Fracture of pelvis without disruption of pelvic circle', 'Fracture of pelvis, other', 'Fracture of femoral neck', 'Fracture of other parts of femur', 'Fracture of patella', 'Fracture of tibia and fibula', 'Fracture of ankle', 'Fracture of LE, other', 'Fracture of clavicle', 'Fracture of scapula', 'Fracture of humerus', 'Fracture of radius and ulna', 'Fracture of Carpal bones', 'Fracture of UE, other', 'TEACHINGSTATUS', 'HOSPITALTYPE', 'Race Complete', 'Race-White', 'Race-Black', 'Race-Other', 'Hispanic', 'BEDSIZE', 'VERIFICATIONLEVEL', 'SEX', 'Sex-Male', 'Sex-Female', 'Sex-Nonbinary', 'GCS', 'primaryecodeicd10', 'fall on same level - other', 'any fall', 'ecode_desc', 'mechanism', 'Mechanism-Fall', 'MVT Motorcyclist', 'MVT Occupant', 'MVT Other', 'MVT Pedal cycli

In [123]:
df.to_csv("cleaned_data_VR.csv", index=False)

In [155]:
df

inc_key                                      LE_Dcode UE_Dcode  \
0       170000016527                                      S82.142A      NaN   
1       170000016539                                      S82.851A      NaN   
2       170000016543                                      S72.142A      NaN   
3       170000016546                                      S72.021A      NaN   
4       170000016550  S92.352A,S82.235A,S82.432A,S82.234A,S82.431A      NaN   
...              ...                                           ...      ...   
766901  230079462361                             S72.354A,S82.61XB      NaN   
766903  230079462392                             S82.141A,S82.831A      NaN   
766904  230079462410                                      S72.335A      NaN   
766905  230079462413                                      S72.092A      NaN   
766906  230079462417                                      S72.011A      NaN   

       Fracture Type   ILE    MLE    ULE  Fracture of acetabulum  \
0                ILE  True  False  False                   False   
1                ILE  True  False  False                   False   
2                ILE  True  False  False                   False   
3                ILE  True  False  False                   False   
4                NaN  True  False  False                   False   
...              ...   ...    ...    ...                     ...   
766901           NaN  True  False  False                   False   
766903           NaN  True  False  False                   False   
766904           ILE  True  False  False                   False   
766905           ILE  True  False  False                   False   
766906           ILE  True  False  False                   False   

        Fracture of pubis  Fracture of ilium  ...  \
0                   False              False  ...   
1                   False              False  ...   
2                   False              False  ...   
3                   False              False  ...   
4                   False              False  ...   
...                   ...                ...  ...   
766901              False              False  ...   
766903              False              False  ...   
766904              False              False  ...   
766905              False              False  ...   
766906              False              False  ...   

        Other Mental/Personality Disorder  \
0                                     NaN   
1                                     NaN   
2                                     NaN   
3                                     NaN   
4                                     NaN   
...                                   ...   
766901                                NaN   
766903                                NaN   
766904                                NaN   
766905                               41.0   
766906                                NaN   

        Other Mental/Personality Disorder T-F  Post-Traumatic Stress Disorder  \
0                                       False                             NaN   
1                                       False                             NaN   
2                                       False                             NaN   
3                                       False                             NaN   
4                                       False                             NaN   
...                                       ...                             ...   
766901                                  False                             NaN   
766903                                  False                             NaN   
766904                                  False                             NaN   
766905                                   True                             NaN   
766906                                  False                             NaN   

        Post-Traumatic Stress Disorder T-F  Schizoaffective Disorder  \
0                       

## Misc Code for Debugging and Querying

In [ ]:
#Look up a code 
print(icd10.find("S32.1").description)

#Look up codes for a list of codes
current = sorted(find_unique_codes(list(df['LE_Dcode'].unique()),"S32",5))
print(current)
print_diagnoses(current)

#Find which codes don't have periods
current = sorted(find_unique_codes(list(df['LE_Dcode'].unique()),"S"))
for i in range(len(current)):
    if not "." in current[i]:
        print(current[i])

#print(sorted(find_unique_codes(list(df['LE_Dcode'].unique()),"S",3)))
#print(sorted(find_unique_codes(list(df['LE_Dcode'].unique()),"S72.0",7)))
#print(sorted(find_unique_codes(list(df['UE_Dcode'].unique()),"S",3)))
#print(sorted(find_unique_codes(list(df['UE_Dcode'].unique()),"S",5)))

#print(list(df['Race Complete'].unique()))
#n=77777
#print(df.loc[n,'Race Complete'])
#print(df.loc[n,'Race Filtered'])

#print(list(df['SEX'].unique()))
#print(list(df['Race Complete'].unique()))
#print(list(df['primarymethodpayment'].unique()))

#str(list(df['SEX'].unique())[2]) == 'nan'
#str(list(df['primarymethodpayment'].unique())[7] ) == 'nan'
#df.loc[df["Race Complete"] == "Other"][["Race Complete","Race-White","Race-Black","Race-Other","Hispanic"]]

#print(sorted(list(df['GCS'].unique())))

#current = sorted(find_unique_codes(list(df['primaryecodeicd10'].unique()),"Y31",8))
#print_diagnoses(current)

#names=['Deep Vein Thrombosis','Alcohol Withdrawal Syndrome','Cardiac Arrest','Catheter-Associated Urinary Tract Infection',
#       'Pulmonary Embolism','Extremity Compartment Syndrome','Unplanned Intubation','Acute Kidney Injury','Myocardial Infarction_hc',
#       'Organ/Space SSI','Osteomyelitis','Other_hc','ARDS','Unplanned Visit to OR','Severe Sepsis','Stroke/CVA',
#       'Superficial Incisional SSI','Pressure Ulcer','Unplanned admission to ICU','Ventilator-Associated Pneumonia']
#for i in names:
#    print(list(df[i].unique()))

#df.loc[df["Substance Abuse Disorder"].isnull()]

In [202]:
icd10.find("S82.231A").description

'Displaced oblique fracture of shaft of right tibia, initial encounter for closed fracture'